In [1]:
import pandas as pd 
import os 
import numpy
import json 

In [2]:
# training_commit_samples.csv, bug_doc_clean.json 

In [3]:
df = pd.read_csv("../data/training_commits_samples.csv")
df.columns 

Index(['Commit ID', 'total_files', 'deleted_files', 'testing', 'maintenance',
       'build', 'csha', 'commit message'],
      dtype='object')

## Prerprocess commit message 

In [4]:
csha_list = df['csha'].values
csha_list[0]

'008cd8a209564a958e9065a5f6ff05526a41f4a5'

In [5]:
import nltk
nltk.download('stopwords')
nltk.download('words')
nltk.download('wordnet')
from nltk.corpus import stopwords
from ast import literal_eval
import re

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/rebecca/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package words to /Users/rebecca/nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/rebecca/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [6]:
GIT_SVN_RE = re.compile('git-svn-id:.*\n')
issue_number_re = re.compile('[A-Za-z]+[-]\d+')
created_by_moe = re.compile('Created by MOE:.*\n')
MOE_ID = re.compile('MOE_MIGRATED_REVID=.*\n')
developer_name_re = re.compile('\(.*\)\n')
HTTP_RE = re.compile('(http|https):.*\n')
EMAIL_RE = re.compile('[a-zA-Z0-9]+@[a-zA-Z0-9]+\.[a-zA-Z0-9-.]+')
Other_RE = re.compile('(Author|Authors|Reviewers|Reviewer).*\n')
Bracket_RE = re.compile('\[.*\]')

break_line_re = re.compile('\n')
digital = re.compile('[0-9]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z ]')
STOPWORDS = set(stopwords.words('english'))

In [7]:
def text_prepare(text):
    """
        text: a string
        
        return: modified initial string
    """
    text = GIT_SVN_RE.sub('', text)
    text = issue_number_re.sub('', text)
    text = created_by_moe.sub('', text)
    text = MOE_ID.sub('', text)
    text = developer_name_re.sub('\n', text)
    text = HTTP_RE.sub('\n', text)
    text = EMAIL_RE.sub('\n', text)
    text = Other_RE.sub('', text)
    text = Bracket_RE.sub('', text)

    text = text.lower()  # lowercase text
    text = break_line_re.sub(' ', text)  # remove all \n
    text = digital.sub('', text)
    text = BAD_SYMBOLS_RE.sub(
        '', text)  # delete symbols which are in BAD_SYMBOLS_RE from text

    text = ' '.join([x for x in text.split() if x and x not in STOPWORDS
                     ])  # delete stopwords from text
    return text

In [8]:
test_commit = df['commit message'].values[232]
print(test_commit)
test_commit = text_prepare(test_commit)
print(test_commit)

AVRO-321.  Restore java RPC interop tests.

git-svn-id: https://svn.apache.org/repos/asf/hadoop/avro/trunk@906635 13f79535-47bb-0310-9956-ffa450edef68

restore java rpc interop tests


In [9]:
df['commit message'] = [text_prepare(line) for line in df['commit message']]
for index, line in enumerate(df['commit message'].values):
    if index < 10:
        print(index, line)

0 merge pull request thiruapachethiru added tests fixed couple bugs also formatted code
1 datafilewriterappendto leads intermittent ioexception write
2 java add command line tool generate schema files protocol contributed bertrand dechoux
3 timeconversions implement getrecommendedschema closes signedoffby gabor szadovszky signedoffby sacharya signedoffby nandor kollar
4 java fix genericdatarecordequals correctly compare schemas fix schemaequals consider order
5 java fix decimal conversion bytebuffer
6 java add support snappy codec newer mapreduce api contributed matt mead
7 improve invalid file format error message
8 java fix builder api correctly handle default values enums
9 java permit maven find imports within project contributed alexandre normand


### Spell Checking 

In [10]:
!pip install pyenchant

You should consider upgrading via the 'pip install --upgrade pip' command.


In [11]:
from enchant.checker import SpellChecker
chkr = SpellChecker("en_US")
wrong_words = []
for index, text in enumerate(df['commit message']):
    chkr.set_text(text)
    for err in chkr:
        if err.word not in wrong_words:
            wrong_words.append(err.word)
        #   print(index, err.word)


def remove_noise_words(message_array):
    res = []
    for text in message_array:
        text = ' '.join(
            [x for x in text.split() if x and x not in wrong_words])
        res.append(text)
    return res


def replace_nosie_words_with_sth(message_array):
    res = []
    for text in message_array:
        # replace wrong word with something
        new_text = []
        for x in text.split():
            if x and x in wrong_words:
                new_text.append('something')
            else:
                new_text.append(x)

        text = ' '.join(new_text)
        res.append(text)
    return res


remove_noise_message = remove_noise_words(df['commit message'].values)
for index, line in enumerate(remove_noise_message):
    if index < 10:
        print(index, line)

0 merge pull request added tests fixed couple bugs also formatted code
1 leads intermittent write
2 add command line tool generate schema files protocol contributed
3 implement closes
4 fix correctly compare fix consider order
5 fix decimal conversion
6 add support snappy newer contributed mead
7 improve invalid file format error message
8 fix builder correctly handle default values
9 permit maven find imports within project contributed


In [12]:
replaced_message = replace_nosie_words_with_sth(df['commit message'].values)
for index, line in enumerate(replaced_message):
    if index < 10:
        print(index, line)

0 merge pull request something added tests fixed couple bugs also formatted code
1 something leads intermittent something write
2 something add command line tool generate schema files protocol contributed something something
3 something implement something closes something something something something something something something something
4 something fix something correctly compare something fix something consider order
5 something fix decimal conversion something
6 something add support snappy something newer something something contributed something mead
7 improve invalid file format error message
8 something fix builder something correctly handle default values something
9 something permit maven find imports within project contributed something something


In [15]:
import numpy as np
original_commit_message = np.copy(df['commit message'])
df['commit message'] = remove_noise_message

## Word Stemming

In [20]:
from nltk.stem import SnowballStemmer
stemmer = SnowballStemmer("english")  # Choose a language
# stemmer.stem("countries")
for index, text in enumerate(df['commit message']):
    print(index, df['commit message'][index])
    df['commit message'][index] = ' '.join(
        [stemmer.stem(x) for x in text.split()])
#     print(index, df['cmt_msg'][index])

0 merg pull request ad test fix coupl bug also format code
1 lead intermitt write
2 add command line tool generat schema file protocol contribut
3 implement close
4 fix correct compar fix consid order
5 fix decim convers
6 add support snappi newer contribut mead
7 improv invalid file format error messag


/Users/rebecca/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


8 fix builder correct handl default valu
9 permit maven find import within project contribut
10 make contribut
11 let job use multipl job contribut
12 chang escap forward slash contribut forehand
13 fix compil drop alias string
14 revert fix support logic type revert commit incorrect key
15 fix support multipl differ contribut
16 make generat specif class work case maven shade use
17 make public
18 creat list schema symbol specifi size
19 add unit test tether contribut
20 fail recogn promot contribut ander
21 extend permit specif proxi contribut
22 add support infin default valu float doubl
23 add implement
24 fix bug print nest record
25 fix mistak error messag contribut beech
26 fix print within null
27 fix protocol reflect reject interfac multipl method name
28 never use
29 fix maven support string type overrid contribut fletcher
30 add payload data context use contribut
31 add support alias
32 fix default constructor correct refer contribut
33 inner loop function
34 remov author ad

198 permit reflect specif datum reader read data written differ version schema current
199 add compress data file
200 redo guava shade compil
201 fix deadlock read replac parser symbol constructor factori method
202 fix possibl memori leak contribut
203 fix better use generic contribut
204 add respons error case
205 add miss licens rat pass also add file exclud sinc permit comment
206 fix order call contribut
207 fix incompat schema detect nest union contribut
208 add span storag
209 remov trace facil seem unus sourc build problem
210 fix abl write back array also fix reflect correct read field
211 optim access messag field
212 fix bug handl thrift short union contribut
213 race condit fingerprint code
214 updat histogram stat
215 data file corrupt recoveri tool contribut
216 improv trace
217 revert fix get correct logic type convers revert commit incorrect key
218 
219 optim handshak protocol
220 schema fingerprint vari local
221 add support read write instanc protocol buffer generat 

404 fix equal work object contain map
405 improv generat contribut
406 revert sinc broke build
407 fix union null contribut
408 add python support read block data contribut
409 valid error messag contribut harsh j
410 add miss licens header
411 add protocol support induc tool
412 fix compil regener code contribut john
413 fix connect thread exit rather client close connect
414 remov unus field import contribut
415 add set remov method contribut chase
416 date test fail timezon match local default
417 remov empti file
418 fix support logic type
419 record name except generat bad code
420 handl default valu record well
421 add debug log invalid logic type contribut
422 work byte close
423 fix bug escap charact contribut
424 add time type specif compil add depend time compil compil class generat class convers regist compil instanc use close
425 incomplet implement use generic schema travers
426 new work
427 support thrift union
428 control commit
429 fix bug record schema contribut
430 te

...

61348 counter keeps track last update adds counter keeps track last time incremented fixes
61349 merge pull request add overloads take
61350 fix illegal reflective access optimization reuse character array used later loses benefit anyway string representation changed byte
61351 merge pull request benchmark performance id creation
61352 merge pull request allow adding removing composite
61353 merge pull request fix auto bind
61354 override propagate fixes change overrides propagate methods registry always ensure indeed would follow flag could result exceptions due type errors since one id registry
61355 merge pull request use empty map null
61356 merge pull request added support metrics
61357 make active overloads consistent others updates overloaded helper methods active consistent counters timers distribution summaries old passive methods deprecated user use instead
61358 merge pull request move package
61359 cleanup use deprecated method counters test
61360 fix end time reported
6136

61443 fix code samples fixes method names used two code samples also removes links deprecated methods
61444 fix incorrectly returning null instead set measurements
61445 remove method deprecated back shows internal usage remaining
61446 ensure variant used
61447 separate concurrent phases move concurrent phases new timer makes easier use pause time see stop world pauses also makes behavior match description docs fixes
61448 refactoring respect contract aggregating values id
61449 add overloads take part cleanup effort finalize deprecated favor provided since extends code registering custom would compile fine however compiled x earlier tried running would get exception thread main change adds back overloads registry fix binary compatibility issue adds test case uses class compiled previous version well try remove deprecated methods classes done without much havoc internally
61450 merge pull request update settings
61451 fix corrupt tag set using offset input string array getting increme

61530 add configuration setting digest compression
61531 merge pull request remove registry
61532 merge pull request rename accessors
61533 merge pull request cleanup comments
61534 address issues flagged
61535 fixing possible race condition registering refactoring aggregate return
61536 fix collector function incorrectly getting applied causing always unknown also updates tests tag value extraction bit smaller focused
61537 ensure polling stops registry reaped registry gets garbage collected task polling get stopped part change longer uses instance updates pick fix private methods used via lambdas getting flagged unused
61538 remove interesting would better use dedicated registry implementation rather trying listen registry
61539 merge pull request remove system initialized
61540 revert improve type safety reverts commit
61541 fix license headers
61542 switch wrap main registry would get included via service loader part composite convenient testing causes everything use digest timers 

61600 merge pull request fix corrupt tag set using
61601 clarify usage method caused confusion internal external users see mail thread context
61602 remove unused import
61603 improve error message method set improves error message indicate method set instead failing later attempting add null tag value id also updates fill default value method null user call explicitly
61604 merge pull request fix issue
61605 fix license header
61606 merge pull request bump versions
61607 cache hash code tag set tag set immutable recomputing hash code time necessary makes much faster perform subsequent lookups id instance
61608 add support timers using dynamic counter code reduce boilerplate code duplication
61609 merge pull request cleanup comments composite classes
61610 move package add tests moves data expression evaluation package easier experimentation also implements equals various helper objects make debugging easier
61611 merge pull request remove listener sending events
61612 add test case te

61704 merge pull request skip bad records
61705 merge pull request reduce log level debug
61706 fix auto bind recent changes causing auto bind fail exceptions like info installing creation errors implementation bound locating parameter locating parameter locating parameter changes auto bind pull spectator module rather separate singleton class also removes prevented test case failing exception
61707 remove interesting would better use dedicated registry implementation rather trying listen registry
61708 merge pull request improve support
61709 allow comma separated list resources running agent arguments comma separated list load
61710 reduce code duplication timers
61711 merge pull request indicate type prefix value
61712 merge pull request make public
61713 allow port eureka overridden
61714 support query data allows agent configured query arbitrary data sample provided test cases bit light right generated using dumps actual data need cleaned sanitized first done later without blockin

In [ ]:
from nltk.stem import WordNetLemmatizer
wnl = WordNetLemmatizer()
# for index, text in enumerate(df['cmt_msg']):
for i in range(len(df['commit message'])):
    print(i, df['commit message'][i])
    df['commit message'][i] = ' '.join(
        [wnl.lemmatize(x) for x in df['commit message'][i].split()])
#     print(i, df['commit message'][i])

0 merg pull request ad test fix coupl bug also format code


/Users/rebecca/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


1 lead intermitt write
2 add command line tool generat schema file protocol contribut
3 implement close
4 fix correct compar fix consid order
5 fix decim conver
6 add support snappi newer contribut mead
7 improv invalid file format error messag
8 fix builder correct handl default valu
9 permit maven find import within project contribut
10 make contribut
11 let job use multipl job contribut
12 chang escap forward slash contribut forehand
13 fix compil drop alia string
14 revert fix support logic type revert commit incorrect key
15 fix support multipl differ contribut
16 make generat specif class work case maven shade use
17 make public
18 creat list schema symbol specifi size
19 add unit test tether contribut
20 fail recogn promot contribut ander
21 extend permit specif proxi contribut
22 add support infin default valu float doubl
23 add implement
24 fix bug print nest record
25 fix mistak error messag contribut beech
26 fix print within null
27 fix protocol reflect reject interfac mult

193 ad document
194 add properti support
195 fix type promot succeed long float
196 addendum fix violat
197 improv perform
198 permit reflect specif datum reader read data written differ version schema current
199 add compress data file
200 redo guava shade compil
201 fix deadlock read replac parser symbol constructor factori method
202 fix possibl memori leak contribut
203 fix better use generic contribut
204 add respon error case
205 add miss licen rat pass also add file exclud sinc permit comment
206 fix order call contribut
207 fix incompat schema detect nest union contribut
208 add span storag
209 remov trace facil seem unus sourc build problem
210 fix abl write back array also fix reflect correct read field
211 optim access messag field
212 fix bug handl thrift short union contribut
213 race condit fingerprint code
214 updat histogram stat
215 data file corrupt recoveri tool contribut
216 improv trace
217 revert fix get correct logic type conver revert commit incorrect key
218 
2

402 add permit stream job easili write format output byte schema contribut tom white
403 deadlock
404 fix equal work object contain map
405 improv generat contribut
406 revert sinc broke build
407 fix union null contribut
408 add python support read block data contribut
409 valid error messag contribut harsh j
410 add miss licen header
411 add protocol support induc tool
412 fix compil regen code contribut john
413 fix connect thread exit rather client close connect
414 remov unus field import contribut
415 add set remov method contribut chase
416 date test fail timezon match local default
417 remov empti file
418 fix support logic type
419 record name except generat bad code
420 handl default valu record well
421 add debug log invalid logic type contribut
422 work byte close
423 fix bug escap charact contribut
424 add time type specif compil add depend time compil compil class generat class conver regist compil instanc use close
425 incomplet implement use generic schema traver
426 ne

...

4290 
4291 close file creat constructor bug
4292 merg r name code most r also see follow revi r wed may line modifi redirect user common configur advanc need r sat line remov deprec class code
4293 make
4294 deprec
4295 use long instead int
4296 add miss
4297 updat remov
4298 move iter interfac main packag
4299 revert use final revert commit
4300 overrid equal match compar contract
4301 chang v
4302 updat relea inform next rather
4303 fix close paragraph element
4304 fix method conform interfac specif modifi constructor throw start index rang adverti ad test case
4305 improv capac handl check larg map
4306 use generic equat
4307 remov trail space
4308 fix warn relat
4309 fix traver call remov thank report patch
4310 improv per
4311 improv document
4312 fix email address link
4313 remov buffer interfac
4314 fix iter remov work proper call previous bug
4315 renam add test fix bug
4316 remov trail space
4317 add miss sinc tag
4318 better handl sublist make type final
4319 deprec new versi

4514 add miss overrid
4515 ad test remov unne import tweak
4516 updat
4517 fix bug add test
4518 add sinc tag
4519 add miss
4520 fix problem
4521 updat deprec messag
4522 redund use public modifi
4523 pr document requir use compar
4524 calcul threshold put data avoid memori issu bug report
4525 code tidi
4526 add collat zip rever method add
4527 remov serial support identifi unsaf class collect branch
4528 add fix typo remov refer bag
4529 merg r name code most r also see follow revi r line ad patch seem pretti reason check project work
4530 merg r name code most r also see follow revi r sat line remov r sat line use covari return type
4531 
4532 add fix typo
4533 replac buffer
4534 harmon signatur factori method collect array base method generic bound thank frank
4535 statement unnecessarili nest within el claus
4536 ensur valu view handl remov element bug
4537 make per
4538 privat immut field might well final
4539 catch error may occur use incorrect use debug bug bug
4540 deprec avai

4738 increment anyth read
4739 ad exampl
4740 base
4741 make extend
4742 fix final code catch except code id previous fix remov variabl unus
4743 fix bug
4744 add support decompress decrypt z archiv format
4745 expand allow read bit
4746 archiv empti file
4747 implement clone way suppo yes broken know final theori subclass may exist overrid clone call would longer popul subclass field proper
4748 better support
4749 document chang
4750 actual read content data descriptor
4751 restor
4752 implement write block checksum
4753 provid pointer sever place
4754 get rid
4755 buffer bound stream better perform
4756 add remain implement provid
4757 check close nonexist entri
4758 remov return void method
4759 unus import
4760 look write file block default
4761 add miss deprec annot
4762 document call
4763 organ import
4764 
4765 provid close method stream
4766 actual close stream promi
4767 version protect version well
4768 know concept also take count ignor
4769 improv except messag long
4770 


4956 trail space
4957 add match method
4958 r broke immut
4959 give tar data work
4960 third case seven known size compress write random access file
4961 except
4962 ad class thread safe creat thread actual compress somewhat effort sinc cannot reliabl read field furthermor achiev true maximum perform would requir zip header creat parallel part compress run possibl prior commit clear thread semant cater futur algorithm improv may want tri take perform edg achiev understand next
4963 add frame
4964 improv readabl
4965 correct use paramet patch appli
4966 move snappi packag make packag privat
4967 expo stream offset size
4968 paramet fill longer use
4969 correct
4970 slight reduc memori pressur
4971 read id x tar
4972 whitespac
4973 revamp support custom compress level header
4974 tar ant task absolut path insid archiv requir allow creation entri
4975 cosmet
4976 renam someon come better name
4977 renam privat field avoid multipl name clash field paramet
4978 add licen header
4979 merg br

5178 unus import
5179 whitespac
5180 replac semant clearer
5181 add preliminari support write z archiv
5182 avoid modifi impli context interfac method public definit
5183 invalid refer doubl quot refer use syntax line
5184 add big file use gnu tar exten write support ad later base patch john
5185 make comment list format match state implement
5186 declar except actual thrown constructor
5187 support skip frame
5188 fix effect
5189 ad field comment
5190 content checksum frame
5191 remov unnecessari cast
5192 tag second compress
5193 clean need return set need make synchron set moment
5194 make happier
5195 infrastructur encod file name tar
5196 ensur zip featur kept minimum entri need
5197 document intend implement
5198 reduc constant issu
5199 check close nonexist entri
5200 appli patch
5201 check case either
5202 support frame snappi format
5203 need nest el block
5204 overrid remov accid
5205 silenc sonar disagr
5206 general except throw list alreadi
5207 need local var
5208 first cu

In [23]:
df.to_csv('training_cmt_after_preprocess_2.csv',index=False)

## Keywords Distribution 
##### (i) Removed custom words: 
e.g ('patch', 'hbase', 'checksum', 'code', 'version', 'byte', 'data', 'hfile', 'region', 'schedul', 'singl', 'can',
'yarn', 'contribut', 'commit', 'merg', 'make', 'trunk', 'hadoop', 'svn', 'ignoreancestri', 'node', 'also', 'client', 'hdfs', 'mapreduc', 'lipcon', 'idea', 'common', 'file', 'ideadev', 'plugin', 'project', 'modul', 'find', 'border', 'addit', 'changeutilencod', 'clickabl', 'color', 'column', 'cach', 'jbrule', 'drool', 'coprocessor', 'regionserv', 'scan', 'resourcemanag', 'cherri', 'gong', 'ryza', 'sandi', 'xuan', 'token', 'contain', 'shen', 'todd', 'zhiji', 'tan', 'wangda', 'timelin', 'app', 'kasha', 'kashacherri', 'messag', 'spr', 'camel', 'http', 'now', 'class', 'default', 'pick', 'via')

##### (ii) We selected 51 most frequent words per class (p.s threshold variable) 

In [ ]:
from scipy import sparse as sp_parse 
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import Counter

In [ ]:
words_counts = Counter()

for words in remove_noise_message:
    for word in words.split():
        words_counts[word] += 1

most_common_words_without_noise = sorted(words_counts.items(),
                                         key=lambda x: x[1],
                                         reverse=True)[:20]

print('Most common words total:')
for word in most_common_words_without_noise:
    print(word)

In [ ]:
tags_counts = Counter()
X, y = df['commit_message'].values, df['class'].values
for tags in y:
    tags_counts[tags] += 1
most_common_tags = sorted(tags_counts.items(),
                          key=lambda x: x[1],
                          reverse=True)[:-1]
most_common_tags

In [ ]:
classes_ = df['class'].value_counts().index

In [ ]:
most_frequent_words_cat = dict()
for cl in classes_:
    print("=====================")
    print(cl)
    commit_messages_cl = df[df['class'] == cl]['commit_message'].values

    words_counts = Counter()

    for words in commit_messages_cl:
        hash_dict = dict()
        for word in words.split():
            if word not in hash_dict and custom_words_set:  # remove VCS words in boosting paper
                hash_dict[word] = True
                words_counts[word] += 1
            else:
                pass

    most_common_words = sorted(words_counts.items(),
                               key=lambda x: x[1],
                               reverse=True)[:300]
    most_frequent_words_cat[cl] = most_common_words

    for word in most_common_words:
        print(word)

for key, vals in most_frequent_words_cat.items():
    print(key)
    for val in vals:
        print(val)

In [ ]:
def get_class_length(dictionary_obj):
    '''
    return:  returns dictionary with class lengths 
    '''
    class_length = dict(
    )  # length of dictionary values in most_frequent_words_cat
    for key, vals in most_frequent_words_cat.items():
        count = 0
        for val in vals:
            count += 1
        class_length[key] = count
    return class_length


# smallest class 'MDL'

In [ ]:
threshold = 51  # threshold for the number of keywords
for key, vals in most_frequent_words_cat.items():
    temp_list = []
        temp_list = vals[:threshold]
    else:
        temp_list = vals
    most_frequent_words_cat[key] = temp_list

class_length = get_class_length(most_frequent_words_cat)
for key, val in class_length.items():
    print(key, val)

## TRIMMING FREQUENT WORDS

In [ ]:
temp_list = []
for key, vals in most_frequent_words_cat.items():
    for val, _ in vals:
        temp_list.append(val)
unique_keywords_words_cat = set(temp_list)
print(len(unique_keywords_words_cat))
print(" ")

for val in unique_keywords_words_cat:
    print(val)

In [ ]:
key_words_features = np.zeros((926, len(unique_keywords_words_cat)))
unique_keywords_words_cat = list(unique_keywords_words_cat)
key_words_features_dict = dict()
for val in unique_keywords_words_cat:
    key_words_features_dict[val] = unique_keywords_words_cat.index(val)

for key, val in key_words_features_dict.items():
    print(key, val)

In [ ]:
for idx, commit in enumerate(df['commit_message'].values):
    commit = commit.split()
    for word in commit:
        if word in key_words_features_dict.keys():
            key_words_features[idx, key_words_features_dict[word]] = 1
np.set_printoptions(precision=2)
print(key_words_features[1, :])